In [ ]:
## reference https://huggingface.co/learn/nlp-course/en/chapter7/6?fw=pt#training-a-causal-language-model-from-scratch

In [1]:
!pip install -U spacy[cuda]

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     |████████████████████████████████| 6.7 MB 9.6 MB/s eta 0:00:01
     |████████████████████████████████| 50 kB 105.7 MB/s eta 0:00:01
     |████████████████████████████████| 193 kB 111.4 MB/s eta 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 494 kB 120.4 MB/s eta 0:00:01
     |████████████████████████████████| 1.8 MB 98.4 MB/s eta 0:00:01
     |████████████████████████████████| 10.2 MB 105.3 MB/s eta 0:00:01
     |████████████████████████████████| 47 kB 93.3 MB/s eta 0:00:01
  Created wheel for cupy: filename=cupy-12.3.0-cp38-cp38-linux_x86_64.whl size=91688965 sha256=feb71193855d095dbcf95e20a0613759bd4f822d03d4a355bc81272a29cd740e
  Stored in directory: /tmp/pip-ephem-wheel-cache-5hww7tlh/wheels/2e/58/a0/8edaf90eec5a5419570ae5ad52bbd480590878dc58897b3360
  Created wheel for thinc: fil

In [96]:
#installing some libraries
!pip install datasets
!pip install --upgrade jupyter ipywidgets



Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [33]:
import matplotlib.pyplot as plt
import seaborn as sns
import torch
import transformers
import spacy

from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer
from transformers import PreTrainedModel, PretrainedConfig
from transformers import AutoModel, AutoConfig,AutoModelForCausalLM, AutoConfig,GPT2Config,BertLMHeadModel
import torch.nn as nn
import torch.nn.functional as F
#from datasets import load_dataset
import pandas as pd, numpy as np
from torch.cuda.amp import autocast
from torch import cuda
import datetime
import warnings,itertools
from torch.optim.lr_scheduler import LambdaLR
import json
# Ignore all warnings
warnings.filterwarnings('ignore')
#pip install transformers bitsandbytes>=0.39.0 -q
import zipfile,logging

In [9]:
import torch
from transformers import GPT2LMHeadModel, GPT2Tokenizer, GPT2Config,BertTokenizer
from nltk import pos_tag, word_tokenize
import nltk
from nltk.corpus import wordnet
import random

# Download necessary NLTK data
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [4]:
#global params for training

B,T = 64,1024
epoch = 100
random_init_wts = True
min_text_len = 0
# train_loss_list = []
# val_loss_list =[]
if cuda.is_available():
    device = torch.device('cuda:0')
    print(device)
else:
    device = 'cpu'
#print(device)
import os
os.environ["TOKENIZERS_PARALLELISM"] = "true"
#os.environ["MKL_DEBUG_CPU_TYPE"] = "5"

#print(global_tr_loss)
model_path = os.path.join("model")
print(model_path)

cuda:0
model


In [5]:
directory = os.path.join('.','data','unzip_text_10M')  # Replace with your directory path
directory

'./data/unzip_text_10M'

In [6]:
def read_text(directory):
    directory = os.path.join('.','data','unzip_text_10M',str(directory))  # Replace with your directory path
    print(f"directory :{directory}")
    # List all files in the directory
    files = [f for f in os.listdir(directory) if os.path.isfile(os.path.join(directory, f))]
    print(f"files:{files}")
    text_content = []
    # Read each file
    total_lines = 0
    for filenum,filename in enumerate(files):
        file_path = os.path.join(directory, filename)
        with open(file_path, 'r', encoding='utf-8') as file:
            #first_line = file.read()
            #print(f"filename :{filename}->first few lines {first_line}")
            #continue
            #lines_list = [line.strip() for line in open(file_path, 'r')]
            text = file.read()
            text_content.append(text)
            print(f"the file:{filename} has been appeneded to the uber list and its length is {len(text_content)} ")
            #total_lines+=len(lines_list)
            #text_content.append(lines_list)
    
    flattened_list = ''.join(text_content)
    assert (len(flattened_list) == total_lines , f"Expected {len(flattened_list)} to be equal to {total_lines}" )
    
    return flattened_list

    

In [7]:
train_list = read_text("train_10M")
#print(train_dict)
#val_list = read_text("dev")

directory :./data/unzip_text_10M/train_10M
files:['switchboard.train', 'simple_wiki.train', 'open_subtitles.train', 'gutenberg.train', 'childes.train', 'bnc_spoken.train']
the file:switchboard.train has been appeneded to the uber list and its length is 1 
the file:simple_wiki.train has been appeneded to the uber list and its length is 2 
the file:open_subtitles.train has been appeneded to the uber list and its length is 3 
the file:gutenberg.train has been appeneded to the uber list and its length is 4 
the file:childes.train has been appeneded to the uber list and its length is 5 
the file:bnc_spoken.train has been appeneded to the uber list and its length is 6 


In [8]:
len(train_list)

54215049

In [9]:
chunks = len(train_list)//(B*T)
print(chunks)

827


In [41]:
tokenizer = BertTokenizer.from_pretrained("vblagoje/bert-english-uncased-finetuned-pos",return_tensors = "pt" , truncate = True, return_overflowing_tokens=True , padding = False,)
#tokenizer = GPT2Tokenizer.from_pretrained("gpt2",return_tensors = "pt" , truncate = True, return_overflowing_tokens=True , padding = False,)


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [42]:
val_list = read_text("dev")


directory :./data/unzip_text_10M/dev
files:['switchboard.dev', 'simple_wiki.dev', 'open_subtitles.dev', 'gutenberg.dev', 'childes.dev', 'bnc_spoken.dev']
the file:switchboard.dev has been appeneded to the uber list and its length is 1 
the file:simple_wiki.dev has been appeneded to the uber list and its length is 2 
the file:open_subtitles.dev has been appeneded to the uber list and its length is 3 
the file:gutenberg.dev has been appeneded to the uber list and its length is 4 
the file:childes.dev has been appeneded to the uber list and its length is 5 
the file:bnc_spoken.dev has been appeneded to the uber list and its length is 6 


In [43]:
enc_train = tokenizer(train_list)


Token indices sequence length is longer than the specified maximum sequence length for this model (15079368 > 512). Running this sequence through the model will result in indexing errors


In [44]:
comp_ratio = len(train_list)/len(enc_train['input_ids'])
comp_ratio

3.5953130794340984

In [45]:
enc_val = tokenizer(val_list)

In [46]:
def get_df_from_list(enc , B= B, T = T, val= False):
    chunk_size = B*T
    if val:
        chunk_size = 2*B*T
        
    long_list_inp = enc['input_ids']
    long_list_attention = enc['attention_mask']

    # Step 3: Split the list into chunks and pad the last chunk if necessary
    chunks_inp = [long_list_inp[i:i + chunk_size] for i in range(0, len(long_list_inp), chunk_size)]
    chunks_att = [long_list_attention[i:i + chunk_size] for i in range(0, len(long_list_attention), chunk_size)]
    df = pd.DataFrame({'input_ids': chunks_inp,'attention_mask':chunks_att})
    return df
    

In [47]:
df_train_temp = get_df_from_list(enc_train)
# Display the DataFrame
df_train_temp.head()
print(f"Length of the dataframe is = {len(df_train_temp)}")

Length of the dataframe is = 231


In [48]:
df_val_temp = get_df_from_list(enc_val)
# Display the DataFrame
df_val_temp.head()
print(f"Length of the VALDATION dataframe is = {len(df_val_temp)}")


Length of the VALDATION dataframe is = 235


In [49]:
def pad_df(df,eos_char = tokenizer.eos_token_id,B = B, T = T,val = False):
    if val:
        B = 2*B
    for ind,row in df.iterrows():
        if len(row['input_ids']) != B*T :
            print(f"row = {ind} and input_id length = {len(row['input_ids'])}")
            print(f"row = {ind} and attention length = {len(row['attention_mask'])}")
            pad_len = B*T - len(row['input_ids'])
            print(f"padding the row index {ind} with {pad_len} character")
            row['input_ids'] = row['input_ids']+ [eos_char] * pad_len
            #attention mask should be padded to 0
            row['attention_mask'] = row['attention_mask']+ [0] * pad_len
            print("#### POST CONCAT####")
            print(f"row = {ind} and input_id length = {len(row['input_ids'])}")
            print(f"row = {ind} and attention length ={len(row['attention_mask'])}")
    return df


def verify_len(df,val = False, B= B):
    row_ind = []
    if val:
        B = 2*B
    for ind,row in df.iterrows():
        if len(row['input_ids']) != B*T :
            row_ind.append(ind)
        else:
            continue
    if len(row_ind) !=0:
        print("CONCATENATION Did not work")
    else:
        print("CONCATENATION worked")
        
            
        
    
        
        
   
   

In [50]:
df_train  = pad_df(df_train_temp)
verify_len(df_train)

row = 230 and input_id length = 6088
row = 230 and attention length = 6088
padding the row index 230 with 59448 character
#### POST CONCAT####
row = 230 and input_id length = 65536
row = 230 and attention length =65536
CONCATENATION worked


In [51]:
df_val  = pad_df(df_val_temp)
verify_len(df_val)

row = 234 and input_id length = 29419
row = 234 and attention length = 29419
padding the row index 234 with 36117 character
#### POST CONCAT####
row = 234 and input_id length = 65536
row = 234 and attention length =65536
CONCATENATION worked


In [52]:
df_train.head()

input_ids  \
0  [101, 1037, 1024, 1045, 1005, 1049, 2469, 2027...   
1  [1055, 3599, 2157, 1012, 1037, 1024, 2092, 101...   
2  [1012, 1037, 1024, 1998, 1999, 2440, 10233, 10...   
3  [2009, 2515, 2061, 4817, 1999, 1037, 1024, 199...   
4  [1027, 10590, 19817, 23049, 10486, 1027, 1027,...   

                                      attention_mask  
0  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
1  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
2  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
3  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
4  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...

In [62]:
# Load GPT-2 model and tokenizer
from transformers import pipeline
model_name = "bert-base-uncased"
#tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name , is_decoder = True)

# Load SpaCy model for POS tagging
pos_model_name = "vblagoje/bert-english-uncased-finetuned-pos"
pos_pipeline = pipeline("token-classification", model=pos_model_name, tokenizer=tokenizer, device = device)

Some weights of the model checkpoint at vblagoje/bert-english-uncased-finetuned-pos were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [64]:
from nltk.corpus import wordnet

def get_pos_tags_bert(tokenizer, input_ids):
    tokens = tokenizer.convert_ids_to_tokens(input_ids)
    words = tokenizer.convert_tokens_to_string(tokens).split()
    pos_tags = pos_pipeline(words)
    print(pos_tags)
    token_pos_map = {tokenizer.convert_tokens_to_ids(tokenizer.tokenize(tag['word']))[0]: tag['entity'] for tag in pos_tags}
    return token_pos_map

def get_verb_synonyms(word):
    synonyms = []
    for syn in wordnet.synsets(word, pos=wordnet.VERB):
        for lemma in syn.lemmas():
            if lemma.name() != word:
                synonyms.append(lemma.name())
    return synonyms


In [65]:
def prepare_input_with_synonym_embeddings(input_ids, model, tokenizer = tokenizer, replacement_prob=0.5):
    model.to('cuda')
    input_ids = torch.tensor(input_ids).to('cuda')
    with torch.no_grad():
        original_embeddings = model.bert.embeddings(input_ids).clone()

    token_pos_map = get_pos_tags_bert(tokenizer, input_ids)
    embed_list = []

    for i, token_id in enumerate(input_ids):
        token_id = token_id.item()
        if token_pos_map.get(token_id, '') == 'VERB' and random.random() < replacement_prob:
            word = tokenizer.decode([token_id])
            synonyms = get_verb_synonyms(word)
            print(f"token_id = {token_id}|word = {word}|synonym = {synonym}")
            if synonyms:
                print("********************")
                synonym = random.choice(synonyms)
                print(f"token_id = {token_id}|word = {word}|synonym = {synonym}|chosen_synonym ={synonym}")
                synonym_tokens = tokenizer.encode(synonym, add_special_tokens=False)
                with torch.no_grad():
                    synonym_embeddings = model.bert.embeddings(torch.tensor(synonym_tokens).to('cuda'))
                mean_synonym_embedding = synonym_embeddings.mean(dim=0)
                embed_list.append(mean_synonym_embedding)
            else:
                embed_list.append(model.bert.embeddings(torch.tensor([token_id]).to('cuda')).squeeze(0))
        else:
            embed_list.append(model.bert.embeddings(torch.tensor([token_id]).to('cuda')).squeeze(0))

    return torch.stack(embed_list)


In [66]:
class BertWithCustomEmbeddings(BertLMHeadModel):
    def forward(self, input_ids=None, attention_mask=None, token_type_ids=None, position_ids=None, head_mask=None, inputs_embeds=None, encoder_hidden_states=None, encoder_attention_mask=None, labels=None, past_key_values=None, use_cache=None, output_attentions=None, output_hidden_states=None, return_dict=None):
        if inputs_embeds is None and input_ids is None:
            raise ValueError("You must pass either input_ids or inputs_embeds")
        
        return super().forward(
            input_ids=input_ids,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            position_ids=position_ids,
            head_mask=head_mask,
            inputs_embeds=inputs_embeds,
            encoder_hidden_states=encoder_hidden_states,
            encoder_attention_mask=encoder_attention_mask,
            labels=labels,
            past_key_values=past_key_values,
            use_cache=use_cache,
            output_attentions=output_attentions,
            output_hidden_states=output_hidden_states,
            return_dict=return_dict
        )

# Instantiate the modified model
custom_model = BertWithCustomEmbeddings.from_pretrained(model_name, is_decoder=True)
model = torch.compile(custom_model)

In [67]:
inp,att = df_train.iloc[2]
type(inp)
token_pos_map = get_pos_tags_bert(tokenizer, torch.tensor(inp).to(device))

[[{'entity': 'PUNCT', 'score': 0.6061594, 'index': 1, 'word': '.', 'start': None, 'end': None}], [{'entity': 'PROPN', 'score': 0.3133451, 'index': 1, 'word': 'a', 'start': None, 'end': None}], [{'entity': 'SYM', 'score': 0.9854855, 'index': 1, 'word': ':', 'start': None, 'end': None}], [{'entity': 'CCONJ', 'score': 0.99890363, 'index': 1, 'word': 'and', 'start': None, 'end': None}], [{'entity': 'ADP', 'score': 0.31213713, 'index': 1, 'word': 'in', 'start': None, 'end': None}], [{'entity': 'ADJ', 'score': 0.99769527, 'index': 1, 'word': 'full', 'start': None, 'end': None}], [{'entity': 'NOUN', 'score': 0.9980919, 'index': 1, 'word': 'faction', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.99372673, 'index': 1, 'word': ',', 'start': None, 'end': None}], [{'entity': 'PROPN', 'score': 0.9427827, 'index': 1, 'word': 'b', 'start': None, 'end': None}], [{'entity': 'SYM', 'score': 0.9854855, 'index': 1, 'word': ':', 'start': None, 'end': None}], [{'entity': 'PRON', 'score': 0.9

TypeError: list indices must be integers or slices, not str

In [93]:
pos_tag = [[{'entity': 'PROPN', 'score': 0.42163557, 'index': 1, 'word': 't', 'start': None, 'end': None}], [{'entity': 'VERB', 'score': 0.997809, 'index': 1, 'word': 'read', 'start': None, 'end': None}], [{'entity': 'SCONJ', 'score': 0.9511905, 'index': 1, 'word': 'that', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.6061594, 'index': 1, 'word': '.', 'start': None, 'end': None}], [{'entity': 'PROPN', 'score': 0.9427827, 'index': 1, 'word': 'b', 'start': None, 'end': None}], [{'entity': 'SYM', 'score': 0.9854855, 'index': 1, 'word': ':', 'start': None, 'end': None}], [{'entity': 'INTJ', 'score': 0.99570125, 'index': 1, 'word': 'oh', 'start': None, 'end': None}], [{'entity': 'INTJ', 'score': 0.9964502, 'index': 1, 'word': 'yeah', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.6061594, 'index': 1, 'word': '.', 'start': None, 'end': None}], [{'entity': 'PROPN', 'score': 0.3133451, 'index': 1, 'word': 'a', 'start': None, 'end': None}], [{'entity': 'SYM', 'score': 0.9854855, 'index': 1, 'word': ':', 'start': None, 'end': None}], [{'entity': 'CCONJ', 'score': 0.99890363, 'index': 1, 'word': 'and', 'start': None, 'end': None}], [{'entity': 'PRON', 'score': 0.9666959, 'index': 1, 'word': 'they', 'start': None, 'end': None}], [{'entity': 'VERB', 'score': 0.9842978, 'index': 1, 'word': 'thought', 'start': None, 'end': None}], [{'entity': 'SCONJ', 'score': 0.9511905, 'index': 1, 'word': 'that', 'start': None, 'end': None}], [{'entity': 'VERB', 'score': 0.82592046, 'index': 1, 'word': 'was', 'start': None, 'end': None}], [{'entity': 'ADJ', 'score': 0.9825149, 'index': 1, 'word': 'more', 'start': None, 'end': None}], [{'entity': 'ADJ', 'score': 0.9979381, 'index': 1, 'word': 'beneficial', 'start': None, 'end': None}], [{'entity': 'SCONJ', 'score': 0.99405646, 'index': 1, 'word': 'because', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.99372673, 'index': 1, 'word': ',', 'start': None, 'end': None}], [{'entity': 'PRON', 'score': 0.99816656, 'index': 1, 'word': 'you', 'start': None, 'end': None}], [{'entity': 'VERB', 'score': 0.9960912, 'index': 1, 'word': 'know', 'start': None, 'end': None}], [{'entity': 'PRON', 'score': 0.99778, 'index': 1, 'word': 'it', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.99372673, 'index': 1, 'word': ',', 'start': None, 'end': None}], [{'entity': 'PRON', 'score': 0.99778, 'index': 1, 'word': 'it', 'start': None, 'end': None}], [{'entity': 'PUNCT', 'score': 0.99372673, 'index': 1, 'word': ',', 'start': None, 'end': None}], [{'entity': 'DET', 'score': 0.99563366, 'index': 1, 'word': 'some', 'start': None, 'end': None}], [{'entity': 'INTJ', 'score': 0.2728758, 'index': 1, 'word': 'of', 'start': None, 'end': None}]]
for ind,tag in enumerate(pos_tag):
    print(f"ind ={ind}|tag = {tag}")
    print(f"word = {tag[0]['word']:tag[0]['entity']}")
    


ind =0|tag = [{'entity': 'PROPN', 'score': 0.42163557, 'index': 1, 'word': 't', 'start': None, 'end': None}]


ValueError: Invalid format specifier

In [58]:
emb = prepare_input_with_synonym_embeddings(inp, model)

IndexError: tuple index out of range

In [ ]:
def write_file(log_message, model_name = "GPT2" ,random_init_wts = random_init_wts ):
    current_datetime = datetime.datetime.now()
    # Extract date and time components
    current_date = str(current_datetime.date())
    log_file = model_name +'_COS_SIM_'+'random_init_wts'+ '_'+str(random_init_wts)+'_' +current_date+'.log'
    print(f"*****LOGGING INFO IN {log_file}*********")
    filepath = os.path.join("model",log_file)
    logging.basicConfig(filename=filepath, 
                    filemode='a',  # Overwrite the log file each time
                    format='%(asctime)s - %(levelname)s - %(message)s', 
                    level=logging.DEBUG)
    logger = logging.getLogger()
    logger.info(log_message)
    
    

    
    

In [ ]:
def prepare_input_with_synonym_embeddings(input_ids, model, tokenizer, token_pos_map, replacement_prob=0.5):
    model.to('cuda')
    input_ids = input_ids.to('cuda')  # Move input_ids to GPU once

    with torch.no_grad():
        original_embeddings = model.transformer.wte(input_ids).clone()

    embed_list = []

    for i, token_id in enumerate(input_ids):
        token_id = token_id.item()  # Convert tensor to integer
        if token_pos_map.get(token_id, '').startswith('VB') and random.random() < replacement_prob:
            word = tokenizer.decode([token_id])
            synonyms = get_verb_synonyms(word)

            if synonyms:
                synonym = random.choice(synonyms)
                synonym_tokens = tokenizer.encode(synonym, add_special_tokens=False)

                with torch.no_grad():
                    synonym_embeddings = model.transformer.wte(torch.tensor(synonym_tokens).to('cuda'))

                mean_synonym_embedding = synonym_embeddings.mean(dim=0)
                embed_list.append(mean_synonym_embedding)

            else:
                embed_list.append(model.transformer.wte(torch.tensor([token_id]).to('cuda')).squeeze(0))
        else:
            embed_list.append(model.transformer.wte(torch.tensor([token_id]).to('cuda')).squeeze(0))

    return torch.stack(embed_list)

In [ ]:
class dataset_pyt_train(Dataset):
    def __init__(self, df, B = B, T = T, model = model, tokenizer = tokenizer, token_pos_map = create_token_pos_mapping(tokenizer)):
        self.df = df
        print(f"Value of B {B}")
                                        
    def __getitem__(self, idx):
        #print(f"inside loader...idx ->{idx}")
        input_id_temp = torch.tensor(self.df.iloc[idx]['input_ids'],dtype = torch.long).to(device)
        att_mask = torch.tensor(self.df.iloc[idx]['attention_mask'],dtype = torch.long).to(device)
        #if the input index is even get the replacement embedding
        
        if idx %2 == 0:
            inp_emb= prepare_input_with_synonym_embeddings(input_id_temp, model = model, tokenizer = tokenizer, token_pos_map = create_token_pos_mapping(tokenizer), replacement_prob=0.1)
        else:
            inp_emb = model.transformer.wte(input_id_temp)
            
                
        inp_emb =   inp_emb.view(-1,T,768)    
        attention_mask = att_mask.view(B,T)   
        labels = input_id_temp.view(B,T)
        return inp_emb, attention_mask,labels
        
    def __len__(self):
        #return the length of the dataframe
        return len(self.df)

### Data loaders and Dataset for batched training

In [ ]:
class dataset_pyt_train(Dataset):
    def __init__(self, df, B = B, T = T, model = model, tokenizer = tokenizer, token_pos_map = create_token_pos_mapping(tokenizer)):
        self.df = df
        print(f"Value of B {B}")
                                        
    def __getitem__(self, idx):
        #print(f"inside loader...idx ->{idx}")
        input_id_temp = torch.tensor(self.df.iloc[idx]['input_ids'],dtype = torch.long).to(device)
        att_mask = torch.tensor(self.df.iloc[idx]['attention_mask'],dtype = torch.long).to(device)
        #if the input index is even get the replacement embedding
        
        if idx %2 == 0:
            inp_emb= prepare_input_with_synonym_embeddings(input_id_temp, model = model, tokenizer = tokenizer, token_pos_map = create_token_pos_mapping(tokenizer), replacement_prob=0.1)
        else:
            inp_emb = model.transformer.wte(input_id_temp)
            
                
        inp_emb =   inp_emb.view(-1,T,768)    
        attention_mask = att_mask.view(B,T)   
        labels = input_id_temp.view(B,T)
        return inp_emb, attention_mask,labels
        
    def __len__(self):
        #return the length of the dataframe
        return len(self.df)

In [ ]:
class dataset_pyt_val(Dataset):
    def __init__(self, df, B = B, T = T, model = model ):
        self.df = df
                                        
    def __getitem__(self, idx):
        #print(f"inside loader...idx ->{idx}")
        input_id_temp = torch.tensor(self.df.iloc[idx]['input_ids'],dtype = torch.long).to(device)
        att_mask = torch.tensor(self.df.iloc[idx]['attention_mask'],dtype = torch.long).to(device)
               
        model.to(device)
        inp_emb = model.transformer.wte(input_id_temp)
        inp_emb =   inp_emb.view(-1,T,768)    
        attention_mask = att_mask.view(B,T)   
        labels = input_id_temp.view(B,T)
        return inp_emb, attention_mask,labels
        
    def __len__(self):
        #return the length of the dataframe
        return len(self.df)

In [ ]:
#train_dataset = dataset_pyt(filtered_df,tokenizer = tokenizer)
train_dataset = dataset_pyt_train(df_train)
val_dataset = dataset_pyt_val(df_val)
#test_dataset = dataset_pyt(df_test,tokenizer = tokenizer)

train_loader = DataLoader(train_dataset,batch_size = 1, shuffle = True , num_workers = 0, pin_memory = False)
val_loader = DataLoader(val_dataset,batch_size = 1, shuffle = True , num_workers = 0, pin_memory = False)
#test_loader = DataLoader(test_dataset,batch_size = batch_size, shuffle = False, collate_fn = custom_collate_fn)


In [ ]:
print(f"Length of the train loader is {len(train_loader)}")
print(f"Length of the val loader is {len(val_loader)}")
print(f"num_tokens= {B*T*len(train_loader)}")

In [ ]:
#emb,att,inp = train_dataset[1]

In [ ]:
class check_train_metrics:
    def __init__(self, patience=10, min_delta=0 , B = T, T = T,best_loss = torch.inf,early_stop = False):
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_loss = best_loss
        self.early_stop = early_stop
        self.B = B
        self.T = T
        self.improvement = None

    def __call__(self, loss, epoch , epoch_durn, norm , current_lr, num_token):
        if self.best_loss - loss > self.min_delta:
            
            print(f"training loss has decreased---> reducing the best loss from {self.best_loss:.2f} to {loss:.2f} | throughput = {int(num_token/epoch_durn)} tokens/second | norm = {norm:.4f} | learning rate = {current_lr:.5e}")
            self.best_loss = loss
            self.counter = 0
            self.improvement = True
        else:
            self.counter += 1
            self.improvement = False
            print(f"No improvement in training  loss-->epoch= {epoch} and best loss is {self.best_loss:.2f}|current_loss = {loss}|counter = {self.counter}")
            if self.counter >= self.patience:
                self.early_stop = True


In [ ]:
class check_val_metrics:
    def __init__(self, patience=5, min_delta=0, best_loss = torch.inf,early_stop = False):
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_loss = best_loss
        self.early_stop = early_stop
        

    def __call__(self, loss, epoch , model, tokenizer):
        if self.best_loss - loss > self.min_delta:
            print(f"Val loss has decreased -->reducing the global validation loss from {self.best_loss:.2f} to {loss:.2f}")
            s1 = (f"Val loss has decreased -->reducing the global validation loss from {self.best_loss:.2f} to {loss:.2f}")
            print(f" validation loss for epoch = {epoch} is {loss:.4f}")
            self.best_loss = loss
            s2 = f" validation loss for epoch = {epoch} is {loss:.4f}"
            print(f" epoch= {epoch} :  val loss is {loss:.4f} ")
            s3 = f" epoch= {epoch} :  val loss is {loss:.4f} "
            #save the model
            # Get the current date and time
            current_datetime = datetime.datetime.now()
            # Extract date and time components
            current_date = str(current_datetime.date())
            current_time = str(current_datetime.time()).split('.')[0]
            file_name = 'model'+ current_date+current_time+'.pth'
            path = os.path.join("model",file_name)
            print(f"saving the model {file_name}")
            s4 = f"saving the model {file_name}"
            #torch.save(model.state_dict(), path)
            model.save_pretrained(path)
            tokenizer.save_pretrained(path)
            log_message = s1+s2+s3+s4
            write_file(log_message)
            self.counter = 0
        else:
            self.counter += 1
            print(f"No improvement in validation loss-->epoch= {epoch} and best val loss is {self.best_loss:.2f}|current_Val loss = {loss}|counter = {self.counter}")
            if self.counter >= self.patience:
                self.early_stop = True

In [ ]:
#model_output = model(input_ids = inp ,attention_mask = att, labels = inp)

In [ ]:
@torch.no_grad

def eval_model(val_loader, model, epoch , device = device,tokenizer = tokenizer):
    model.eval()
    model.to(device)
    e = epoch+1
    embedding_layer = model.transformer.wte
    val_loss_accum = 0.0
    print(f"inside validation data for epoch {e}")
    for ind,(input_embed,attention_mask,labels) in enumerate(val_loader):
        emb = torch.squeeze(input_embed,dim = 0)
        emb = emb.to(device=device, non_blocking=True)
        att_mask = torch.squeeze(attention_mask,dim = 0)
        att_mask = att_mask.to(device=device, non_blocking=True)
        labels = torch.squeeze(labels,dim = 0)
        labels = labels.to(device)
        with autocast(dtype = torch.bfloat16):
            model_output = model(inputs_embeds = emb, attention_mask = att_mask, labels = labels)
            #print(f"model_output loss = {model_output.loss}")
            total_loss = model_output.loss  
    
    
    
        val_loss_accum+= total_loss
        del emb,att_mask,labels,model_output,total_loss
    return val_loss_accum        
    
    
    


In [ ]:

def train_model(train_loader,val_loader,model,num_epoch = 30,device = device,tokenizer = tokenizer):
    #model.train()
    device = device
    lr_custom = 1e-6
    print(f"inside train model. Device = {device}")
    model.to(device)
    optimizer = torch.optim.AdamW(params =  model.parameters(), lr= lr_custom,fused = True ,weight_decay = .1)
      
    extra_train = .1*num_epoch
    max_train_steps = int(num_epoch +extra_train )
    import time
    from transformers import get_linear_schedule_with_warmup
    total_steps = len(train_loader) * num_epoch
    scheduler_cos = transformers.get_cosine_schedule_with_warmup( optimizer= optimizer, num_warmup_steps =int(total_steps * 0.1) ,num_training_steps= total_steps )
        
    epoch_train_log = []
    epoch_val_log = []
    validate_val_metric = check_val_metrics()
    validate_train_metric = check_train_metrics(patience=5, min_delta=0 , B = T, T = T)
    for i in range (max_train_steps):
        
        epoch_start_time = time.time()
        optimizer.zero_grad(set_to_none=True)
        # we use 2 schedulers - the first LR scheduler uses a cosine decay for 100 epochs the second scheduler takes the last LR from cosine scheduler and then maintains that LR for the next 10 epochs
        if i >= num_epoch:
            optimizer_reduced_lr = torch.optim.AdamW(params =  model.parameters(), lr= current_lr ,fused = True , weight_decay=.1)
            scheduler_constant = transformers.get_constant_schedule_with_warmup( optimizer = optimizer_reduced_lr ,num_warmup_steps = 0, last_epoch = -1 )
        
        epoch_train_loss = 0       
        for ind,(input_embed,attention_mask,labels) in enumerate(train_loader):
            if ind == int(len(train_loader)/2):
                batch_time = time.time()
                duration = batch_time - epoch_start_time
                print(f"executing epoch:{i+1}, it took {duration/60} mins from beginning of epoch till batch#{ind}")
            
            emb = torch.squeeze(input_embed,dim = 0)
            emb = emb.to(device=device, non_blocking=True)
            att_mask = torch.squeeze(attention_mask,dim = 0)
            att_mask = attention_mask.to(device=device, non_blocking=True)
            labels = torch.squeeze(labels,dim = 0)
            labels = labels.to(device)
                        
            with autocast(dtype = torch.bfloat16):
                model_output = model(inputs_embeds = emb, attention_mask = att_mask, labels = labels)
                if np.isnan(model_output.loss.item()):
                    print("f nan values encountered..")
                    #decoded_texts = [tokenizer.decode(ids, skip_special_tokens=True) for ids in ids]
                    #print(f"*********$$$$$$$$$ decoded_texts = {decoded_texts}*************")
                total_loss =model_output.loss 
                                
            assert not np.isnan(model_output.loss.item()), "NaN value found"
                               
            total_loss.backward()
            epoch_train_loss += total_loss.detach().item()
            norm = torch.nn.utils.clip_grad_norm(model.parameters() , 1.0)
            if i <= num_epoch:
                optimizer.step()
                scheduler_cos.step()
                optimizer.zero_grad(set_to_none=True)
            else:
                optimizer_reduced_lr.step()
                optimizer_reduced_lr.zero_grad(set_to_none=True)
                scheduler_constant.step()
                
                         
            del emb,att_mask,labels,model_output
            
        #batch processing complete 
        #print(f"batch processing complete , lambda = {lambda_val} |total_loss for batch= {total_loss}")
        
        if i <= num_epoch:
            current_lr = scheduler_cos.get_last_lr()[0]
        epoch_end_time = time.time()
        epoch_durn = (epoch_end_time - epoch_start_time)
        num_token = B*T*len(train_loader)
        epoch_train_log.append(epoch_train_loss)
        validate_train_metric(epoch_train_loss, i , epoch_durn, norm , current_lr, num_token)
        
        if validate_train_metric.improvement:
            val_loss= eval_model(val_loader, model, epoch = i, device = device,tokenizer = tokenizer)
            epoch_val_log.append(val_loss)
            validate_val_metric(val_loss, i , model, tokenizer)
            if validate_train_metric.early_stop or validate_val_metric.early_stop :
                print(f"early stopping trigerred either from training data or val data | train_counter = {validate_train_metric.counter}|val_counter = {validate_val_metric.counter}")
                break
        else:
            if validate_val_metric.early_stop:
                print(f"early stopping trigerred from validation data")
                break
              
    
    return model,epoch_train_log,epoch_val_log
        
            
            
    
    

In [ ]:
tr_model,epoch_train_log,epoch_val_log = train_model(train_loader, val_loader,model=tune_model,tokenizer = tokenizer)

In [ ]:
import json , os
path_var_train_log = os.path.join(".","Tokenizers_and_loss_vals","epoch_train_plain_loss.json")
path_var_val_log = os.path.join(".","Tokenizers_and_loss_vals","epoch_val_val_loss_.json")

#print(path_var)
#Write the list to a JSON file
with open(path_var_train_log, "w") as file:
    json.dump(epoch_train_log, file)

with open(path_var_val_log, "w") as file:
    json.dump(epoch_val_log, file)


In [ ]:
with open(path_var_train_log, "r") as file:
    train_loss = json.load(file)
with open(path_var_val_log, "r") as file:
    val_loss = json.load(file)

In [ ]:
x_values = range(len(train_loss))
plt.plot(x_values, train_loss, label='Train_loss')

In [ ]:
x_values_val = range(len(val_loss))
plt.plot(x_values_val, val_loss, label='val_loss')

In [ ]:
min_length = min(len(train_loss), len(val_loss))
list1 = train_loss[:min_length]
list2 = val_loss[:min_length]

# Create x-axis values
x_values = range(min_length)

# Plot the lists
plt.plot(x_values, list1, label='Train_loss')
plt.plot(x_values, list2, label='Val_loss')

# Adding labels and title
plt.xlabel('Epoch')
plt.ylabel('Value')
plt.title('Train Loss and Val_Loss')
plt.legend()